In [11]:
from textwrap import dedent
from agno.agent import Agent
from dotenv import load_dotenv 
from agno.models.openai import OpenAILike
from agno.memory.v2.db.sqlite import SqliteMemoryDb
from agno.memory.v2.memory import Memory
from rich.pretty import pprint
from agno.storage.sqlite import SqliteStorage
from typing import List,Dict
from pydantic import BaseModel, Field
import os
load_dotenv()



True

**agent state**

In [ ]:
# Define a tool that adds an item to the shopping list
def add_item(agent: Agent, item: str) -> str:
    """Add an item to the shopping list."""
    if agent.session_state is None:
        agent.session_state = {}
    if "shopping_list" not in agent.session_state:
        agent.session_state["shopping_list"] = []
    agent.session_state["shopping_list"].append(item)
    return f"The shopping list is now {agent.session_state['shopping_list']}"

agent = Agent(
name="my_agent",
model=OpenAILike(id="qwen3-30b-a3b", 
    api_key=os.getenv("BAILIAN_API_KEY"), 
    base_url=os.getenv("BAILIAN_API_BASE_URL"),
    request_params={"extra_body": {"enable_thinking": False}},),
markdown=True,
# Initialize the session state with a counter starting at 0
session_state={"shopping_list": []},
tools=[add_item],
# You can use variables from the session state in the instructions
instructions="Current state (shopping list) is: {shopping_list}",
# Important: Add the state to the messages
add_state_in_messages=True,
)

# Example usage
agent.print_response("Add milk, eggs, and bread to the shopping list", stream=True)
print(f"Final session state: {agent.session_state}")

Output()

Final session state: {'shopping_list': ['milk', 'eggs', 'bread'], 'current_session_id': 'fb205638-5e39-40e7-8722-1aedcd7995e0'}


In [6]:
# Define tools to manage our shopping list
def add_item(agent: Agent, item: str) -> str:
    """Add an item to the shopping list and return confirmation."""
    # Add the item if it's not already in the list
    if agent.session_state is None:
        agent.session_state = {}
    if "shopping_list" not in agent.session_state:
        agent.session_state["shopping_list"] = []

    # Add the item if it's not already in the list
    if item.lower() not in [i.lower() for i in agent.session_state["shopping_list"]]:
        agent.session_state["shopping_list"].append(item)
        return f"Added '{item}' to the shopping list"
    else:
        return f"'{item}' is already in the shopping list"


def remove_item(agent: Agent, item: str) -> str:
    """Remove an item from the shopping list by name."""
    # Case-insensitive search
    if agent.session_state is None:
        agent.session_state = {}
    if "shopping_list" not in agent.session_state:
        agent.session_state["shopping_list"] = []

    for i, list_item in enumerate(agent.session_state["shopping_list"]):
        if list_item.lower() == item.lower():
            agent.session_state["shopping_list"].pop(i)
            return f"Removed '{list_item}' from the shopping list"

    return f"'{item}' was not found in the shopping list"


def list_items(agent: Agent) -> str:
    """List all items in the shopping list."""
    if agent.session_state is None:
        agent.session_state = {}
    if "shopping_list" not in agent.session_state:
        agent.session_state["shopping_list"] = []
        
    shopping_list = agent.session_state["shopping_list"]

    if not shopping_list:
        return "The shopping list is empty."

    items_text = "\n".join([f"- {item}" for item in shopping_list])
    return f"Current shopping list:\n{items_text}"


# Create a Shopping List Manager Agent that maintains state
agent = Agent(
    model=OpenAILike(id="qwen3-30b-a3b", 
    api_key=os.getenv("BAILIAN_API_KEY"), 
    base_url=os.getenv("BAILIAN_API_BASE_URL"),
    request_params={"extra_body": {"enable_thinking": False}},),
    # Initialize the session state with an empty shopping list
    session_state={"shopping_list": []},
    tools=[add_item, remove_item, list_items],
    # You can use variables from the session state in the instructions
    instructions=dedent("""\
        Your job is to manage a shopping list.

        The shopping list starts empty. You can add items, remove items by name, and list all items.

        Current shopping list: {shopping_list}
    """),
    show_tool_calls=True,
    add_state_in_messages=True,
    markdown=True,
)

# Example usage
agent.print_response("Add milk, eggs, and bread to the shopping list", stream=True)
print(f"Session state: {agent.session_state}")

agent.print_response("I got bread", stream=True)
print(f"Session state: {agent.session_state}")

agent.print_response("I need apples and oranges", stream=True)
print(f"Session state: {agent.session_state}")

agent.print_response("whats on my list?", stream=True)
print(f"Session state: {agent.session_state}")

agent.print_response("Clear everything from my list and start over with just bananas and yogurt", stream=True)
print(f"Session state: {agent.session_state}")

Output()

Session state: {'shopping_list': ['milk', 'eggs', 'bread'], 'current_session_id': '7d5889cc-c85a-46a8-bd6d-617eb4fc56fb'}


Output()

Session state: {'shopping_list': ['milk', 'eggs'], 'current_session_id': '7d5889cc-c85a-46a8-bd6d-617eb4fc56fb'}


Output()

Session state: {'shopping_list': ['milk', 'eggs', 'apples', 'oranges'], 'current_session_id': '7d5889cc-c85a-46a8-bd6d-617eb4fc56fb'}


Output()

Session state: {'shopping_list': ['milk', 'eggs', 'apples', 'oranges'], 'current_session_id': '7d5889cc-c85a-46a8-bd6d-617eb4fc56fb'}


Output()

Session state: {'shopping_list': ['bananas', 'yogurt'], 'current_session_id': '7d5889cc-c85a-46a8-bd6d-617eb4fc56fb'}


**Memory**

In [14]:
# UserId for the memories
user_id = "ava"
# Database file for memory and storage
db_file = "temp/agent.db"

# Initialize memory.v2
memory = Memory(
    # Use any model for creating memories
    model=OpenAILike(id="qwen3-30b-a3b", 
    api_key=os.getenv("BAILIAN_API_KEY"), 
    base_url=os.getenv("BAILIAN_API_BASE_URL"),
    request_params={"extra_body": {"enable_thinking": False}},),
    db=SqliteMemoryDb(table_name="user_memories", db_file=db_file),
)
# Initialize storage
storage = SqliteStorage(table_name="agent_sessions", db_file=db_file)

# Initialize Agent
memory_agent = Agent(
    model=OpenAILike(id="qwen3-30b-a3b", 
    api_key=os.getenv("BAILIAN_API_KEY"), 
    base_url=os.getenv("BAILIAN_API_BASE_URL"),
    request_params={"extra_body": {"enable_thinking": False}},),
    # Store memories in a database
    memory=memory,
    # Give the Agent the ability to update memories
    enable_agentic_memory=True,
    # OR - Run the MemoryManager after each response
    enable_user_memories=True,
    # Store the chat history in the database
    storage=storage,
    # Add the chat history to the messages
    add_history_to_messages=True,
    # Number of history runs
    num_history_runs=3,
    markdown=True,
)

memory.clear()
memory_agent.print_response(
    "My name is Ava and I like to ski.",
    user_id=user_id,
    stream=True,
    stream_intermediate_steps=True,
)
print("Memories about Ava:")
pprint(memory.get_user_memories(user_id=user_id))

memory_agent.print_response(
    "I live in san francisco, where should i move within a 4 hour drive?",
    user_id=user_id,
    stream=True,
    stream_intermediate_steps=True,
)
print("Memories about Ava:")
pprint(memory.get_user_memories(user_id=user_id))

Output()

Memories about Ava:


[
│   UserMemory(
│   │   memory='Ava likes to ski.',
│   │   topics=['name', 'hobbies'],
│   │   input='My name is Ava and I like to ski.',
│   │   last_updated=datetime.datetime(2025, 7, 14, 17, 48, 3, 101965),
│   │   memory_id='c97cfac1-5166-49c3-b002-dac0530182ab'
│   )
]

Output()

Memories about Ava:


[
│   UserMemory(
│   │   memory='Ava likes to ski.',
│   │   topics=['name', 'hobbies'],
│   │   input='My name is Ava and I like to ski.',
│   │   last_updated=datetime.datetime(2025, 7, 14, 17, 48, 3, 101965),
│   │   memory_id='c97cfac1-5166-49c3-b002-dac0530182ab'
│   )
]

**structured output**

In [13]:
class MovieScript(BaseModel):
    setting: str = Field(
        ..., description="Provide a nice setting for a blockbuster movie."
    )
    ending: str = Field(
        ...,
        description="Ending of the movie. If not available, provide a happy ending.",
    )
    genre: str = Field(
        ...,
        description="Genre of the movie. If not available, select action, thriller or romantic comedy.",
    )
    name: str = Field(..., description="Give a name to this movie")
    characters: List[str] = Field(..., description="Name of characters for this movie.")
    storyline: str = Field(
        ..., description="3 sentence storyline for the movie. Make it exciting!"
    )
    rating: Dict[str, int] = Field(
        ...,
        description="Your own rating of the movie. 1-10. Return a dictionary with the keys 'story' and 'acting'.",
    )


# Agent that uses structured outputs with streaming
structured_output_agent = Agent(
    model=OpenAILike(id="qwen3-30b-a3b", 
        api_key=os.getenv("BAILIAN_API_KEY"), 
        base_url=os.getenv("BAILIAN_API_BASE_URL"),
        request_params={"extra_body": {"enable_thinking": False}},),
    description="You write movie json scripts.",
    response_model=MovieScript,
)

structured_output_agent.print_response(
    "New York", stream=True, stream_intermediate_steps=True
)

Output()

WARNING  Failed to parse cleaned JSON: 6 validation errors for MovieScript                                         
         setting                                                                                                   
           Input should be a valid string [type=string_type, input_value={'location': 'New York Ci...t hold hidden 
         stories.'}, input_type=dict]                                                                              
             For further information visit https://errors.pydantic.dev/2.11/v/string_type                          
         ending                                                                                                    
           Field required [type=missing, input_value={'title': 'New York', 'ge...s a central character.'},         
         input_type=dict]                                                                                          
             For further information visit https://errors.pydantic.dev/2.11/v/missing                              
         name                                                                                                      
           Field required [type=missing, input_value={'title': 'New York', 'ge...s a central character.'},         
         input_type=dict]                                                                                          
             For further information visit https://errors.pydantic.dev/2.11/v/missing                              
         characters                                                                                                
           Field required [type=missing, input_value={'title': 'New York', 'ge...s a central character.'},         
         input_type=dict]                                                                                          
             For further information visit https://errors.pydantic.dev/2.11/v/missing                              
         storyline                                                                                                 
           Field required [type=missing, input_value={'title': 'New York', 'ge...s a central character.'},         
         input_type=dict]                                                                                          
             For further information visit https://errors.pydantic.dev/2.11/v/missing                              
         rating                                                                                                    
           Field required [type=missing, input_value={'title': 'New York', 'ge...s a central character.'},         
         input_type=dict]                                                                                          
             For further information visit https://errors.pydantic.dev/2.11/v/missing

WARNING  Validation failed on merged data: 6 validation errors for MovieScript                                     
         setting                                                                                                   
           Input should be a valid string [type=string_type, input_value={'location': 'New York Ci...t hold hidden 
         stories.'}, input_type=dict]                                                                              
             For further information visit https://errors.pydantic.dev/2.11/v/string_type                          
         ending                                                                                                    
           Field required [type=missing, input_value={'setting': {'location': ...genre': 'Drama / Crime'},         
         input_type=dict]                                                                                          
             For further information visit https://errors.pydantic.dev/2.11/v/missing                              
         name                                                                                                      
           Field required [type=missing, input_value={'setting': {'location': ...genre': 'Drama / Crime'},         
         input_type=dict]                                                                                          
             For further information visit https://errors.pydantic.dev/2.11/v/missing                              
         characters                                                                                                
           Field required [type=missing, input_value={'setting': {'location': ...genre': 'Drama / Crime'},         
         input_type=dict]                                                                                          
             For further information visit https://errors.pydantic.dev/2.11/v/missing                              
         storyline                                                                                                 
           Field required [type=missing, input_value={'setting': {'location': ...genre': 'Drama / Crime'},         
         input_type=dict]                                                                                          
             For further information visit https://errors.pydantic.dev/2.11/v/missing                              
         rating                                                                                                    
           Field required [type=missing, input_value={'setting': {'location': ...genre': 'Drama / Crime'},         
         input_type=dict]                                                                                          
             For further information visit https://errors.pydantic.dev/2.11/v/missing

WARNING  All parsing attempts failed.

WARNING  Failed to convert response to response_model